In [1]:
import xarray as xr
import pandas as pd
import progressbar
import numpy as np
from oggm.utils import mkdir
import matplotlib.pyplot as plt

In [2]:
%pwd

'/home/www/fmaussion/runs/runs_diff_calib_protect'

### GCMs - missing glaciers overview 

In [3]:
dirpath = './output'

In [4]:
import os
allfiles = []
for root, dirs, files in os.walk(dirpath):
    for file in files:
        if file.endswith(".nc"):
             allfiles.append(os.path.join(root, file))

In [5]:
allfiles = sorted(allfiles)
allfiles[:10]

['./output/match_geod/RGI01/BCC-CSM2-MR/BCC-CSM2-MR_ssp126.nc',
 './output/match_geod/RGI01/BCC-CSM2-MR/BCC-CSM2-MR_ssp245.nc',
 './output/match_geod/RGI01/BCC-CSM2-MR/BCC-CSM2-MR_ssp370.nc',
 './output/match_geod/RGI01/BCC-CSM2-MR/BCC-CSM2-MR_ssp585.nc',
 './output/match_geod/RGI01/CAMS-CSM1-0/CAMS-CSM1-0_ssp119.nc',
 './output/match_geod/RGI01/CAMS-CSM1-0/CAMS-CSM1-0_ssp126.nc',
 './output/match_geod/RGI01/CAMS-CSM1-0/CAMS-CSM1-0_ssp245.nc',
 './output/match_geod/RGI01/CAMS-CSM1-0/CAMS-CSM1-0_ssp370.nc',
 './output/match_geod/RGI01/CAMS-CSM1-0/CAMS-CSM1-0_ssp585.nc',
 './output/match_geod/RGI01/CESM2-WACCM/CESM2-WACCM_ssp126.nc']

In [6]:
rgi_meta = pd.read_hdf('/home/www/oggm/rgi/rgi62_stats.h5')

In [7]:
rgi_meta = rgi_meta.loc[rgi_meta.Connect != 2]

In [9]:
df_meta = pd.DataFrame()
invalid_per_reg = {}  
meta_per_reg = {}

for f in progressbar.progressbar(allfiles):
    ename = f.replace('./output/', '')
    ss = ename.split('/')
    exp = ss[0]
    rgi_reg = ss[1]
    gcm = ss[2]
    ssp = ename.split('.')[-2].split('_')[-1]
    
    if ssp not in ['ssp119', 'ssp126', 'ssp245', 'ssp370', 'ssp585']:
        continue
    
    run_id = f'{exp}:{gcm}:{ssp}:{rgi_reg}'
    df_meta.loc[run_id, 'exp'] = exp
    df_meta.loc[run_id, 'gcm'] = gcm
    df_meta.loc[run_id, 'ssp'] = ssp
    df_meta.loc[run_id, 'rgi_reg'] = rgi_reg
    df_meta.loc[run_id, 'end_year'] = 0
    df_meta.loc[run_id, 'perc_area_missing'] = 0
    df_meta.loc[run_id, 'fpath'] = f
    
    if rgi_reg not in invalid_per_reg:
        invalid_per_reg[rgi_reg] = set()
    
    if rgi_reg not in meta_per_reg:
        meta_per_reg[rgi_reg] = rgi_meta.loc[rgi_meta['O1Region'] == rgi_reg[-2:]]
    
    with xr.open_dataset(f) as ds:
        df_meta.loc[run_id, 'end_year'] = int(ds.time[-1])
        missing_ids = ds.rgi_id[ds.isel(time=-1).volume.load().isnull()].data
        perc = meta_per_reg[rgi_reg].loc[missing_ids]['Area'].sum() / meta_per_reg[rgi_reg]['Area'].sum() 
        df_meta.loc[run_id, 'perc_area_missing'] = perc
        invalid_per_reg[rgi_reg] = invalid_per_reg[rgi_reg].union(missing_ids)

100% (3591 of 3591) |####################| Elapsed Time: 0:03:33 Time:  0:03:33


In [10]:
dds = df_meta.sort_values('perc_area_missing', ascending=False)
dds[dds['perc_area_missing'] > 0.05].rgi_reg.unique()

array(['RGI12'], dtype=object)

In [11]:
df_meta.to_csv('agg/metadata.csv')

In [12]:
for k, v in invalid_per_reg.items():
    invalid_per_reg[k] = list(v)

In [13]:
import json

In [14]:
with open('agg/rgi_ids_missing.json', 'w') as f:
    json.dump(invalid_per_reg, f)

In [15]:
odf = pd.DataFrame()
for rgi_reg, missing_ids in invalid_per_reg.items():
    odf.loc[rgi_reg, 'n_glaciers'] = len(meta_per_reg[rgi_reg])
    odf.loc[rgi_reg, 'n_missing_glaciers'] = len(missing_ids)
    odf.loc[rgi_reg, 'rgi_area'] = meta_per_reg[rgi_reg]['Area'].sum() 
    odf.loc[rgi_reg, 'missing_area'] = meta_per_reg[rgi_reg].loc[missing_ids]['Area'].sum()
    odf.loc[rgi_reg, 'missing_perc'] = odf.loc[rgi_reg, 'missing_area'] / odf.loc[rgi_reg, 'rgi_area']
odf[['n_glaciers', 'n_missing_glaciers']] = odf[['n_glaciers', 'n_missing_glaciers']].astype(int)
odf

n_glaciers  n_missing_glaciers    rgi_area  missing_area  missing_perc
RGI01       27108                  29   86725.053        19.716      0.000227
RGI02       18855                  87   14524.224         3.848      0.000265
RGI03        4556                  44  105110.642        21.911      0.000208
RGI04        7415                  74   40888.228        24.604      0.000602
RGI05       19306                  99   89717.066        17.381      0.000194
RGI06         568                   2   11059.700         0.271      0.000025
RGI07        1615                   1   33958.934         8.985      0.000265
RGI08        3417                   6    2949.103         0.207      0.000070
RGI09        1069                   3   51591.600        24.421      0.000473
RGI10        5151                 217    2410.051        89.888      0.037297
RGI11        3927                   5    2092.146         0.377      0.000180
RGI12        1888                 339    1306.992       155.814      0.119216
RGI13       54429                 136   49303.415        24.164      0.000490
RGI14       27988                 193   33568.298        34.397      0.001025
RGI15       13119                  81   14734.204       159.040      0.010794
RGI16        2939                  34    2341.036        59.027      0.025214
RGI17       15908                  54   29429.080        23.775      0.000808
RGI18        3537                   0    1161.801         0.000      0.000000
RGI19        2752                 471  132867.219       903.218      0.006798

In [16]:
odf.to_csv('agg/missing_region_overview.csv')
odf.to_html('agg/missing_region_overview.html')

### GCMs - agrregation

In [17]:
base_dir = 'agg/'

In [18]:
df_meta.ssp.unique()

array(['ssp126', 'ssp245', 'ssp370', 'ssp585', 'ssp119'], dtype=object)

In [19]:
ds

<xarray.Dataset>
Dimensions:         (time: 81, rgi_id: 2752)
Coordinates:
  * time            (time) float64 2.02e+03 2.021e+03 ... 2.099e+03 2.1e+03
  * rgi_id          (rgi_id) object 'RGI60-19.00001' ... 'RGI60-19.02752'
    hydro_year      (time) int64 ...
    hydro_month     (time) int64 ...
    calendar_year   (time) int64 ...
    calendar_month  (time) int64 ...
Data variables:
    volume          (time, rgi_id) float32 ...
    volume_bsl      (time, rgi_id) float32 ...
    volume_bwl      (time, rgi_id) float32 ...
    area            (time, rgi_id) float32 ...
    length          (time, rgi_id) float32 ...
    calving         (time, rgi_id) float32 ...
    calving_rate    (time, rgi_id) float32 ...
    water_level     (rgi_id) float32 ...
    glen_a          (rgi_id) float32 ...
    fs              (rgi_id) float32 ...
Attributes:
    description:    OGGM model output
    oggm_version:   1.5.3
    calendar:       365-day no leap
    creation_date:  2022-06-29 15:34:58

In [27]:
for exp in df_meta.exp.unique():
    print(exp, flush=True)
    for rgi_reg in progressbar.progressbar(sorted(df_meta.rgi_reg.unique())):
        for ssp in sorted(df_meta.ssp.unique()):
            df_meta_s = df_meta.loc[(df_meta.exp == exp) & (df_meta.rgi_reg == rgi_reg) & (df_meta.ssp == ssp)]
            odf_v = pd.DataFrame()
            odf_a = pd.DataFrame()
            ods = []
            gcms = []
            for i, s in df_meta_s.iterrows():
                with xr.open_dataset(s.fpath) as ds:
                    ds = ds[['volume', 'area', 'length']].load().isel(rgi_id=~ds.rgi_id.isin(invalid_per_reg[s.rgi_reg]))
                    odf_v[s.gcm] = ds.volume.sum(dim='rgi_id').to_series()
                    odf_a[s.gcm] = ds.area.sum(dim='rgi_id').to_series()
                    ods.append(ds)
                    gcms.append(s.gcm)
            ods = xr.concat(ods, 'gcm')
            ods.mean(dim='gcm').to_netcdf(f'./output/{exp}/{rgi_reg}/all_gcm_avg_{ssp}.nc')
            ods.std(dim='gcm').to_netcdf(f'./output/{exp}/{rgi_reg}/all_gcm_std_{ssp}.nc')
            odir = base_dir + f'volume/{exp}/{rgi_reg}/'
            mkdir(odir)
            odf_v.to_csv(odir + f'{ssp}.csv')
            odir = base_dir + f'area/{exp}/{rgi_reg}/'
            mkdir(odir)
            odf_a.to_csv(odir + f'{ssp}.csv')

match_geod


100% (19 of 19) |########################| Elapsed Time: 0:02:36 Time:  0:02:36


match_geod_pergla


100% (19 of 19) |########################| Elapsed Time: 0:03:11 Time:  0:03:11


no_match


100% (19 of 19) |########################| Elapsed Time: 0:03:38 Time:  0:03:38


In [ ]:
for var in ['volume', 'area']:
    for exp in df_meta.exp.unique():
        odir = base_dir + f'{var}/{exp}/global/'
        mkdir(odir)
        for ssp in sorted(df_meta.ssp.unique()):
            odf = 0
            for rgi_reg in sorted(df_meta.rgi_reg.unique()):
                idir = base_dir + f'{var}/{exp}/{rgi_reg}/'
                df = pd.read_csv(idir + f'/{ssp}.csv', index_col=0)
                odf += df
            odf.to_csv(odir + f'/{ssp}.csv')

In [ ]:
f, axs = plt.subplots(3, 2, figsize=(14, 12), sharey=True)
axs = np.array(axs).flatten()
for ssp, ax in zip(sorted(df_meta.ssp.unique()), axs):
    for exp, c in zip(df_meta.exp.unique(), ['navy', 'royalblue', 'peru']):
        idir = base_dir + f'volume/{exp}/global/'
        df = pd.read_csv(idir + f'/{ssp}.csv', index_col=0)
        avg = df.mean(axis=1) * 1e-9
        std = df.std(axis=1) * 1e-9
        ax.fill_between(avg.index, avg-std, avg+std, alpha=0.3, color=c)
        avg.plot(ax=ax, label=exp, c=c);
    ax.set_title(ssp)
ax.legend();
plt.tight_layout();

In [ ]:
for reg in sorted(df_meta.rgi_reg.unique()):
    f, axs = plt.subplots(2, 2, figsize=(14, 8), sharey=True)
    axs = np.array(axs).flatten()
    for ssp, ax in zip(sorted(df_meta.ssp.unique())[1:], axs):
        for exp, c in zip(df_meta.exp.unique(), ['navy', 'royalblue', 'peru']):
            idir = base_dir + f'volume/{exp}/{reg}/'
            df = pd.read_csv(idir + f'/{ssp}.csv', index_col=0)
            avg = df.mean(axis=1) * 1e-9
            std = df.std(axis=1) * 1e-9
            ax.fill_between(avg.index, avg-std, avg+std, alpha=0.3, color=c)
            avg.plot(ax=ax, label=exp, c=c);
        ax.set_title(ssp)
    ax.legend();
    plt.suptitle(reg)
    plt.tight_layout();

### Historical - aggregation 

In [ ]:
base_dir = 'historical/agg/'

In [ ]:
for exp in df_meta.exp.unique():
    odf_v = pd.DataFrame()
    odf_a = pd.DataFrame()
    for rgi_reg in progressbar.progressbar(sorted(df_meta.rgi_reg.unique())):
        f = f'historical/{exp}/historical_run_output_extended_{rgi_reg[-2:]}.nc'
        with xr.open_dataset(f) as ds:
            volume = ds.volume.load().isel(rgi_id=~ds.rgi_id.isin(invalid_per_reg[s.rgi_reg]))
            odf_v[rgi_reg] = volume.sum(dim='rgi_id').to_series()
            area = ds.area.load().isel(rgi_id=~ds.rgi_id.isin(invalid_per_reg[s.rgi_reg]))
            odf_a[rgi_reg] = area.sum(dim='rgi_id').to_series()
    odir = base_dir + f'volume/{exp}/'
    mkdir(odir)
    odf_v.to_csv(odir + f'historical.csv')
    odir = base_dir + f'area/{exp}/'
    mkdir(odir)
    odf_a.to_csv(odir + f'historical.csv')

In [ ]:
base_dir_gcm = 'agg/'
base_dir_hist = 'historical/agg/'

f, axs = plt.subplots(3, 2, figsize=(14, 12), sharey=True)
axs = np.array(axs).flatten()
for ssp, ax in zip(sorted(df_meta.ssp.unique()), axs):
    for exp, c in zip(df_meta.exp.unique(), ['navy', 'royalblue', 'peru']):
        idir = base_dir_hist + f'volume/{exp}/'
        df = pd.read_csv(idir + f'/historical.csv', index_col=0)
        glob = df.sum(axis=1) * 1e-9
        glob.loc[2000:].plot(ax=ax, label='', c=c);
        
        idir = base_dir_gcm + f'volume/{exp}/global/'
        df = pd.read_csv(idir + f'/{ssp}.csv', index_col=0)
        avg = df.mean(axis=1) * 1e-9
        std = df.std(axis=1) * 1e-9
        ax.fill_between(avg.index, avg-std, avg+std, alpha=0.3, color=c)
        avg.plot(ax=ax, label=exp, c=c);
    ax.set_title(ssp)
ax.legend();
plt.tight_layout();

In [ ]:
base_dir_gcm = 'agg/'
base_dir_hist = 'historical/agg/'

f, axs = plt.subplots(3, 2, figsize=(14, 12), sharey=True)
axs = np.array(axs).flatten()
for ssp, ax in zip(sorted(df_meta.ssp.unique()), axs):
    for exp, c in zip(df_meta.exp.unique(), ['navy', 'royalblue', 'peru']):
        idir = base_dir_hist + f'volume/{exp}/'
        df = pd.read_csv(idir + f'/historical.csv', index_col=0)
        glob = df.sum(axis=1) * 1e-9
        glob.loc[2000:].plot(ax=ax, label='', c=c);
        
        idir = base_dir_gcm + f'volume/{exp}/global/'
        df = pd.read_csv(idir + f'/{ssp}.csv', index_col=0).iloc[:10]
        avg = df.mean(axis=1) * 1e-9
        std = df.std(axis=1) * 1e-9
        ax.fill_between(avg.index, avg-std, avg+std, alpha=0.3, color=c)
        avg.plot(ax=ax, label=exp, c=c);
    ax.set_title(ssp)
ax.legend();
plt.tight_layout();